In [14]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

# Import libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import ast

# Suppress all warnings
import warnings
warnings.filterwarnings('ignore')

# Pandas specific settings to avoid FutureWarnings
pd.set_option('future.no_silent_downcasting', True)

# Optional: Set display options for better output
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)
pd.set_option('display.float_format', '{:.2f}'.format)


# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))


print("Libraries imported successfully!")

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

Libraries imported successfully!


# # Anime Platform Analytics: Understanding Genre, Studio, and User Preferences

## Project Goal

This project analyzes a comprehensive anime dataset to understand how **genres, studios, formats, and release trends** shape popularity and user satisfaction. By exploring content performance metrics and user behavior, we aim to provide actionable insights for content strategy and platform optimization.

## Data Merging & Feature Engineering

Combining multiple datasets to create a comprehensive dataset with enriched features for analysis.

In [15]:
# Load multiple datasets
base_path = 'data/'  # Adjust this path if your datasets are in a different location

# Load main details dataset
df_details = pd.read_csv(base_path + 'details.csv')
print(f"Details dataset shape: {df_details.shape}")

# Load stats dataset (contains viewing statistics)
df_stats = pd.read_csv(base_path + 'stats.csv')
print(f"Stats dataset shape: {df_stats.shape}")

# Load ratings dataset
df_ratings = pd.read_csv(base_path + 'ratings.csv')
print(f"Ratings dataset shape: {df_ratings.shape}")



print("\nDatasets loaded successfully!")

Details dataset shape: (28955, 29)
Stats dataset shape: (28955, 27)
Ratings dataset shape: (124298357, 6)

Datasets loaded successfully!


In [16]:
# Merge details and stats datasets on 'mal_id'
print("Merging datasets...")

df = pd.merge(df_details, df_stats, on='mal_id', how='left')
print(f"After merging details + stats: {df.shape}")
print(f"Columns: {df.columns.tolist()}")

print("\nMerged dataset created successfully!")

Merging datasets...
After merging details + stats: (28955, 55)
Columns: ['mal_id', 'title', 'title_japanese', 'url', 'image_url', 'type', 'status', 'score', 'scored_by', 'start_date', 'end_date', 'synopsis', 'rank', 'popularity', 'members', 'favorites', 'genres', 'studios', 'themes', 'demographics', 'source', 'rating', 'episodes', 'season', 'year', 'producers', 'explicit_genres', 'licensors', 'streaming', 'watching', 'completed', 'on_hold', 'dropped', 'plan_to_watch', 'total', 'score_1_votes', 'score_1_percentage', 'score_2_votes', 'score_2_percentage', 'score_3_votes', 'score_3_percentage', 'score_4_votes', 'score_4_percentage', 'score_5_votes', 'score_5_percentage', 'score_6_votes', 'score_6_percentage', 'score_7_votes', 'score_7_percentage', 'score_8_votes', 'score_8_percentage', 'score_9_votes', 'score_9_percentage', 'score_10_votes', 'score_10_percentage']

Merged dataset created successfully!


In [17]:
import re

print("Original dataset shape:", df.shape)
print("\n\t\tDATA CLEANING\t\t\n")

# 1. Remove anime with only numeric titles (e.g., "123", "456")
print("1. Removing anime with only numeric titles...")
df = df[~df['title'].str.match(r'^\d+$', na=False)]
print(f"   After removing numeric-only titles: {df.shape}")

# 1.5. Remove titles with multiple dots (e.g., "......")
print("1.5. Removing titles with excessive dots/periods...")
df = df[~df['title'].str.contains(r'\.\.+', na=False)]  # 2+ consecutive dots
print(f"   After removing dotted titles: {df.shape}")

# 1.6. Remove timestamp-like patterns (e.g., "00.08", "009-1", "00:00")
print("\n1.6. Removing timestamp-like patterns...")
timestamp_pattern = r'^\d+[:\-\.]\d+.*$|^\d{2,}\-\d+$'
df = df[~df['title'].str.match(timestamp_pattern, na=False)]
print(f"   After removing timestamp patterns: {df.shape}")

# 1.7. Remove titles starting with special characters followed by numbers
print("\n1.7. Removing special character + number patterns (e.g., r&b, etc.)...")
df = df[~df['title'].str.match(r'^[^a-zA-Z]+\d', na=False)]
print(f"   After removing special+number patterns: {df.shape}")

# 1.8. Remove very short titles with only numbers and special chars
print("\n1.8. Removing very short non-alphabetic titles...")
df = df[~((df['title'].str.len() <= 5) & (~df['title'].str.contains(r'[a-zA-Z]{2,}', na=False)))]
print(f"   After removing short non-alpha titles: {df.shape}")

# 2. Remove rows where title contains only special characters or is too short
print("\n2. Removing invalid/very short titles...")
df = df[df['title'].str.len() > 2]
print(f"   After removing short titles: {df.shape}")

# 3. Drop rows with missing critical values (title, type, mal_id)
print("\n3. Removing rows with missing critical values...")
df = df.dropna(subset=['mal_id', 'title', 'type'])
print(f"   After removing critical missing values: {df.shape}")

# 4. Remove duplicate anime based on mal_id
print("\n4. Removing duplicate anime...")
df = df.drop_duplicates(subset=['mal_id'], keep='first')
print(f"   After removing duplicates: {df.shape}")

# 5. Drop irrelevant columns
print("\n5. Removing irrelevant columns...")
irrelevant_cols = ['url', 'image_url', 'title_japanese']  # URLs and Japanese titles not needed for analysis
df = df.drop(columns=[col for col in irrelevant_cols if col in df.columns])
print(f"   After removing irrelevant columns: {df.shape}")

# 6. Clean specific columns
print("\n6. Additional data quality checks...")

# Remove anime with invalid years (future years or too old)
if 'year' in df.columns:
    df = df[(df['year'].isna()) | ((df['year'] >= 1900) & (df['year'] <= 2026))]
    print(f"   After year validation: {df.shape}")

# Remove anime with invalid scores (outside 0-10 range)
if 'score' in df.columns:
    df = df[(df['score'].isna()) | ((df['score'] >= 0) & (df['score'] <= 10))]
    print(f"   After score validation: {df.shape}")

print("\n\t\tCLEANING COMPLETE\t\t\n")
print(f"Final cleaned dataset shape: {df.shape}")
print(f"Rows removed: {28955 - df.shape[0]}")
print(f"\nRemaining missing values per column:")
print(df.isnull().sum().sort_values(ascending=False).head(10))


Original dataset shape: (28955, 55)

		DATA CLEANING		

1. Removing anime with only numeric titles...
   After removing numeric-only titles: (28941, 55)
1.5. Removing titles with excessive dots/periods...
   After removing dotted titles: (28860, 55)

1.6. Removing timestamp-like patterns...
   After removing timestamp patterns: (28847, 55)

1.7. Removing special character + number patterns (e.g., r&b, etc.)...
   After removing special+number patterns: (28728, 55)

1.8. Removing very short non-alphabetic titles...
   After removing short non-alpha titles: (28703, 55)

2. Removing invalid/very short titles...
   After removing short titles: (28690, 55)

3. Removing rows with missing critical values...
   After removing critical missing values: (28624, 55)

4. Removing duplicate anime...
   After removing duplicates: (28624, 55)

5. Removing irrelevant columns...
   After removing irrelevant columns: (28624, 52)

6. Additional data quality checks...
   After year validation: (28624, 52)


In [18]:
# Function to check if a value is an empty list
def is_empty_list(val):
    if pd.isna(val):
        return True
    if isinstance(val, str) and val.strip() in ['[]', '']:
        return True
    if isinstance(val, list) and len(val) == 0:
        return True
    return False

# Calculate percentage of empty lists or NaN for each column
threshold = 0.7
empty_percentages = {}

for col in df.columns:
    empty_count = df[col].apply(is_empty_list).sum()
    empty_percentages[col] = empty_count / len(df)

# Get columns to drop
columns_to_drop = [col for col, pct in empty_percentages.items() if pct > threshold]

print(f"Dropping {len(columns_to_drop)} columns with >{threshold*100}% empty/missing data:")
for col in columns_to_drop:
    print(f"  - {col}: {empty_percentages[col]*100:.1f}% empty")

df = df.drop(columns=columns_to_drop)
print(f"\nDataset shape after dropping columns: {df.shape}")

#Drop rows with high percentage of empty/missing data
row_threshold = 0.5  # Drop rows with >50% empty values
print(f"\nChecking rows with >{row_threshold*100}% empty data...")

# Count empty values per row
empty_per_row = df.apply(lambda row: row.apply(is_empty_list).sum(), axis=1)
empty_percentage_per_row = empty_per_row / len(df.columns)
# Identify rows to drop
rows_to_drop = empty_percentage_per_row > row_threshold
num_rows_to_drop = rows_to_drop.sum()

print(f"Dropping {num_rows_to_drop} rows with >{row_threshold*100}% empty data")

# Drop the rows
df = df[~rows_to_drop].reset_index(drop=True)
print(f"Dataset shape after dropping rows: {df.shape}")

Dropping 5 columns with >70.0% empty/missing data:
  - season: 78.2% empty
  - year: 78.2% empty
  - explicit_genres: 100.0% empty
  - licensors: 82.1% empty
  - streaming: 87.0% empty

Dataset shape after dropping columns: (28624, 47)

Checking rows with >50.0% empty data...
Dropping 368 rows with >50.0% empty data
Dataset shape after dropping rows: (28256, 47)


## Feature Engineering: Creating Calculated Metrics

Now we'll create NEW features by combining existing columns from the merged dataset to enable advanced analysis:
- **Engagement metrics**: completion_rate, drop_rate
- **Polarization metrics**: polarization_index
- **Quality metrics**: score consistency

In [19]:
print("\nFEATURE ENGINEERING\n")
print("Creating new calculated metrics from merged dataset features...\n")

# 1. ENGAGEMENT METRICS (using stats.csv features)
print("1. Creating Engagement Metrics...")

# Completion Rate: percentage of users who completed the anime
df['completion_rate'] = (df['completed'] / df['total'] * 100).fillna(0)

# Drop Rate: percentage of users who dropped the anime
df['drop_rate'] = (df['dropped'] / df['total'] * 100).fillna(0)

# Plan-to-Watch Ratio: interest vs actual viewers
df['ptw_ratio'] = (df['plan_to_watch'] / df['members']).fillna(0)

print(f"   - completion_rate: {df['completion_rate'].mean():.2f}% average")
print(f"   - drop_rate: {df['drop_rate'].mean():.2f}% average")
print(f"   - ptw_ratio: {df['ptw_ratio'].mean():.3f} average")

# 2. POLARIZATION METRICS (using score distribution features)
print("\n2. Creating Polarization Metrics...")

# Polarization Index: sum of extreme ratings (love it or hate it)
df['polarization_index'] = (df['score_10_percentage'] + df['score_1_percentage']).fillna(0)

# Controversy Score: variance in ratings
df['rating_spread'] = (df['score_10_percentage'] - df['score_1_percentage']).fillna(0)

print(f" -- polarization_index: {df['polarization_index'].mean():.2f}% average")
print(f" -- rating_spread: {df['rating_spread'].mean():.2f} average")

# 3. QUALITY CONSISTENCY METRICS
print("\n3. Creating Quality Metrics...")

# High Rating Concentration: % of scores 8-10
df['high_rating_concentration'] = (df['score_8_percentage'] + df['score_9_percentage'] + df['score_10_percentage']).fillna(0)

# Low Rating Concentration: % of scores 1-3  
df['low_rating_concentration'] = (df['score_1_percentage'] + df['score_2_percentage'] + df['score_3_percentage']).fillna(0)

print(f" -- high_rating_concentration: {df['high_rating_concentration'].mean():.2f}% average")
print(f" -- low_rating_concentration: {df['low_rating_concentration'].mean():.2f}% average")

# Extract year from start_date and handle NaN values
df['year'] = pd.to_datetime(df['start_date'], errors='coerce').dt.year

# Extract season from start_date
df['month'] = pd.to_datetime(df['start_date'], errors='coerce').dt.month

# Create proper season column based on month (overwrite if needed)
def assign_season(month):
    if pd.isna(month):
        return None
    elif month in [12, 1, 2]:
        return 'Winter'
    elif month in [3, 4, 5]:
        return 'Spring'
    elif month in [6, 7, 8]:
        return 'Summer'
    elif month in [9, 10, 11]:
        return 'Fall'
    else:
        return None

df['season_derived'] = df['month'].apply(assign_season)

# Use the original season column if available, otherwise use derived
if 'season' not in df.columns or df['season'].isna().sum() > df['season_derived'].isna().sum():
    df['season'] = df['season_derived']

print(f"\nMissing values after extraction:")
print(f"Year: {df['year'].isna().sum()} / {len(df)} ({df['year'].isna().sum()/len(df)*100:.1f}%)")
print(f"Season: {df['season'].isna().sum()} / {len(df)} ({df['season'].isna().sum()/len(df)*100:.1f}%)")


print("\n\t\tFEATURE ENGINEERING COMPLETE\t\t\n")
print(f"New features added: 8 calculated metrics")
print(f"Total columns now: {df.shape[1]}")
print(f"\nNew feature columns: {['completion_rate', 'drop_rate', 'ptw_ratio', 'polarization_index', 'rating_spread', 'high_rating_concentration', 'low_rating_concentration']}" )


FEATURE ENGINEERING

Creating new calculated metrics from merged dataset features...

1. Creating Engagement Metrics...
   - completion_rate: 49.43% average
   - drop_rate: 11.96% average
   - ptw_ratio: 0.295 average

2. Creating Polarization Metrics...
 -- polarization_index: 20.00% average
 -- rating_spread: 8.86 average

3. Creating Quality Metrics...
 -- high_rating_concentration: 30.35% average
 -- low_rating_concentration: 11.86% average

Missing values after extraction:
Year: 628 / 28256 (2.2%)
Season: 628 / 28256 (2.2%)

		FEATURE ENGINEERING COMPLETE		

New features added: 8 calculated metrics
Total columns now: 58

New feature columns: ['completion_rate', 'drop_rate', 'ptw_ratio', 'polarization_index', 'rating_spread', 'high_rating_concentration', 'low_rating_concentration']


In [20]:
df.head(10)

mal_id                                              title     type  \
0   59356                                           -Socket-    Movie   
1    2928                               .hack//G.U. Returner      OVA   
2    3269                                .hack//G.U. Trilogy    Movie   
3    4469                   .hack//G.U. Trilogy: Parody Mode  Special   
4     454                                        .hack//Gift      OVA   
5    1143                                  .hack//Intermezzo  Special   
6     299                                  .hack//Liminality      OVA   
7    9332                                     .hack//Quantum      OVA   
8   10390  .hack//Quantum: Sore ike! Bokura no Chimuchimu...  Special   
9     873                                       .hack//Roots       TV   

            status  score  scored_by                 start_date  \
0  Finished Airing    NaN        NaN  2010-01-01T00:00:00+00:00   
1  Finished Airing   6.65    9745.00  2007-01-18T00:00:00+00:00   
2  Finished Airing   7.06   15373.00  2007-12-22T00:00:00+00:00   
3  Finished Airing   6.35    4317.00  2008-03-25T00:00:00+00:00   
4  Finished Airing   6.09   10021.00  2003-11-16T00:00:00+00:00   
5  Finished Airing   6.51   11616.00  2003-03-28T00:00:00+00:00   
6  Finished Airing   6.58   17130.00  2002-06-20T00:00:00+00:00   
7  Finished Airing   7.11   20412.00  2011-01-28T00:00:00+00:00   
8  Finished Airing   6.29    2810.00  2011-01-28T00:00:00+00:00   
9  Finished Airing   6.85   36216.00  2006-04-06T00:00:00+00:00   

                    end_date  \
0                        NaN   
1                        NaN   
2                        NaN   
3                        NaN   
4                        NaN   
5                        NaN   
6  2003-04-10T00:00:00+00:00   
7  2011-04-07T00:00:00+00:00   
8  2011-04-07T00:00:00+00:00   
9  2006-09-28T00:00:00+00:00   

                                            synopsis     rank  popularity  \
0  A girl with a cord growing out of her back wan... 17086.00       22507   
1  The characters from previous .hack//G.U. Games...  6366.00        5056   
2  Based on the CyberConnect2 HIT GAME, now will ...  4194.00        4215   
3  A special bonus Parody Mode added to the extra...  8182.00        6696   
4  As an expression of gratitude for the heroes o...  9692.00        5162   
5  A virtual multiplayer online role-playing game...  7195.00        4910   
6  While playing the newly released MMORPG "The W...  6740.00        4178   
7  Tobias, Mary, and Sakuya challenge the impregn...  3960.00        3808   
8  DVD specials for .hack//Quantum. Main girls ar...  8559.00        7369   
9  After the termination of the incredibly popula...  5197.00        2718   

   members  favorites                                         genres  \
0      195          0                                     ['Comedy']   
1    22525         31              ['Adventure', 'Drama', 'Fantasy']   
2    34264        104                          ['Action', 'Fantasy']   
3    11135         10                ['Comedy', 'Fantasy', 'Sci-Fi']   
4    21458         20                          ['Comedy', 'Fantasy']   
5    24340          7  ['Adventure', 'Fantasy', 'Mystery', 'Sci-Fi']   
6    34986         35                                    ['Mystery']   
7    42217         72             ['Action', 'Adventure', 'Fantasy']   
8     8835          3                                     ['Comedy']   
9    76863        235              ['Adventure', 'Drama', 'Fantasy']   

             studios                    themes demographics    source  \
0                 []                        []           []  Original   
1      ['Bee Train']            ['Video Game']           []      Game   
2  ['CyberConnect2']            ['Video Game']           []      Game   
3                 []  ['Parody', 'Video Game']           []      Game   
4      ['Bee Train']            ['Video Game']           []  Original   
5      ['Bee Train']         

In [21]:
# Load recommendations dataset
df_recommendations = pd.read_csv(base_path + 'recommendations.csv')
print(f'Recommendations dataset shape: {df_recommendations.shape}')
print(f'Columns: {df_recommendations.columns.tolist()}')
print(df_recommendations.head())

# Load favs dataset  
df_favs = pd.read_csv(base_path + 'favs.csv')
print(f'\nFavs dataset shape: {df_favs.shape}')
print(f'Columns: {df_favs.columns.tolist()}')
print(df_favs.head())

Recommendations dataset shape: (105249, 2)
Columns: ['mal_id', 'recommendation_mal_id']
   mal_id  recommendation_mal_id
0    3269                    317
1    3269                   6922
2    3269                    299
3    3269                   3446
4    3269                   5681

Favs dataset shape: (4178747, 3)
Columns: ['username', 'fav_type', 'id']
    username fav_type     id
0  ishikawas    anime  45649
1  ishikawas    anime  38680
2  ishikawas    anime    795
3  ishikawas    anime  37510
4  ishikawas    anime    820


In [22]:
print("\n=== FEATURE ENGINEERING: Recommendations & Favorites ===")
print("Creating new metrics from recommendation and favorite patterns...\n")

# 1. RECOMMENDATION NETWORK FEATURES
print("1. Creating Recommendation Network Metrics...")
# Count how many times each anime is recommended
recommendation_counts = df_recommendations.groupby('mal_id').size().reset_index(name='recommendation_count')
print(f"   - recommendation_count: Number of times anime appears in recommendations")
print(f"   - Average recommendations per anime: {recommendation_counts['recommendation_count'].mean():.2f}")

# Merge with main dataset
df = df.merge(recommendation_counts, on='mal_id', how='left')
df['recommendation_count'] = df['recommendation_count'].fillna(0)

# 2. USER FAVORITES FEATURES  
print("\n2. Creating User Favorite Metrics...")
# Filter only anime favorites (exclude manga, characters, etc.)
df_anime_favs = df_favs[df_favs['fav_type'] == 'anime'].copy()

# Count how many users favorited each anime
favorite_counts = df_anime_favs.groupby('id').size().reset_index(name='user_favorites_count')
print(f"   - user_favorites_count: Number of users who favorited this anime")
print(f"   - Average favorites per anime: {favorite_counts['user_favorites_count'].mean():.2f}")

# Merge with main dataset
df = df.merge(favorite_counts, left_on='mal_id', right_on='id', how='left')
df['user_favorites_count'] = df['user_favorites_count'].fillna(0)
df = df.drop(columns=['id'], errors='ignore')  # Drop the merge key

# 3. ENGAGEMENT RATIO METRICS
print("\n3. Creating Engagement Ratio Metrics...")
# Recommendation-to-Member Ratio: How recommended is it relative to membership
df['recommendation_ratio'] = (df['recommendation_count'] / df['members']).fillna(0)
print(f"   - recommendation_ratio: Recommendations per member (virality indicator)")
print(f"   - Average: {df['recommendation_ratio'].mean():.4f}")

# Favorites-to-Member Ratio: Favorite intensity
df['favorite_intensity'] = (df['user_favorites_count'] / df['members']).fillna(0)
print(f"   - favorite_intensity: Favorites per member (passion indicator)")
print(f"   - Average: {df['favorite_intensity'].mean():.4f}")

print("\n=== FEATURE ENGINEERING COMPLETE ===")
print(f"New features added: 4 metrics (recommendation_count, user_favorites_count, recommendation_ratio, favorite_intensity)")
print(f"Total columns now: {df.shape[1]}")
print(f"\nDataset shape: {df.shape}")


=== FEATURE ENGINEERING: Recommendations & Favorites ===
Creating new metrics from recommendation and favorite patterns...

1. Creating Recommendation Network Metrics...
   - recommendation_count: Number of times anime appears in recommendations
   - Average recommendations per anime: 11.65

2. Creating User Favorite Metrics...
   - user_favorites_count: Number of users who favorited this anime
   - Average favorites per anime: 152.29

3. Creating Engagement Ratio Metrics...
   - recommendation_ratio: Recommendations per member (virality indicator)
   - Average: 0.0002
   - favorite_intensity: Favorites per member (passion indicator)
   - Average: 0.0003

=== FEATURE ENGINEERING COMPLETE ===
New features added: 4 metrics (recommendation_count, user_favorites_count, recommendation_ratio, favorite_intensity)
Total columns now: 62

Dataset shape: (28256, 62)


---

# ANALYTICAL QUESTIONS & VISUALIZATIONS

---

## Question 1: Hidden Viral Gems Analysis

**Research Question:** Which anime are "Hidden Viral Gems" with high recommendation ratios despite low member counts?

In [23]:
# Q1: Hidden Viral Gems Analysis
# Filter anime with recommendations and members data
df_q1 = df[(df['recommendation_count'] > 0) & (df['members'] > 0) & (df['score'].notna())].copy()

# Define hidden as below median members
median_members = df_q1['members'].median()
df_hidden = df_q1[df_q1['members'] < median_members].copy()

# Find top 15 hidden viral gems
top_hidden_gems = df_hidden.nlargest(20, 'recommendation_ratio')[['title', 'recommendation_ratio', 'members', 'score', 'recommendation_count']]

print("=== TOP 15 HIDDEN VIRAL GEMS ===")
print("(High recommendation ratio despite low member count)")
print()
for idx, row in top_hidden_gems.iterrows():
    title_short = row['title'][:50]
    print(f"{title_short:45} | Ratio: {row['recommendation_ratio']:.4f} | Members: {int(row['members']):,} | Score: {row['score']:.2f}")

print()
print("Analysis:")
print(f"- Median member threshold: {int(median_members):,}")
print(f"- Hidden anime analyzed: {len(df_hidden):,}")
print(f"- Avg rec ratio (hidden): {df_hidden['recommendation_ratio'].mean():.6f}")
print(f"- Avg rec ratio (popular): {df_q1[df_q1['members'] >= median_members]['recommendation_ratio'].mean():.6f}")
print(f"- Top gem: {int(top_hidden_gems.iloc[0]['recommendation_count'])} recs with only {int(top_hidden_gems.iloc[0]['members']):,} members!")

=== TOP 15 HIDDEN VIRAL GEMS ===
(High recommendation ratio despite low member count)

Nagisa no Peppy                               | Ratio: 0.0177 | Members: 226 | Score: 5.45
Find My Color                                 | Ratio: 0.0175 | Members: 228 | Score: 6.32
Revenge of Green Mutant                       | Ratio: 0.0161 | Members: 434 | Score: 5.34
Dog Attacks Human                             | Ratio: 0.0129 | Members: 310 | Score: 5.35
Timeless                                      | Ratio: 0.0116 | Members: 431 | Score: 6.03
Mug                                           | Ratio: 0.0113 | Members: 533 | Score: 5.98
Technology Shamanism                          | Ratio: 0.0104 | Members: 288 | Score: 5.45
B.O.Y.                                        | Ratio: 0.0103 | Members: 388 | Score: 5.42
Yoru no Uta                                   | Ratio: 0.0103 | Members: 291 | Score: 6.24
Yu Tong                                       | Ratio: 0.0100 | Members: 299 | Score: 5.69
Kai

In [24]:
# Enhanced Interactive Visualization for Q1 with Bright Annotation Colors
# Calculate medians first
median_members = df_q1['members'].median()
median_rec_ratio = df_q1['recommendation_ratio'].median()

fig = px.scatter(df_q1, 
                 x='members', 
                 y='recommendation_ratio',
                 color='score',
                 size='recommendation_count',
                 hover_data={
                     'title': True,
                     'score': ':.2f',
                     'members': ':,',
                     'recommendation_count': ':,',
                     'recommendation_ratio': ':.4f'
                 },
                 title='Hidden Viral Gems: Recommendation Efficiency vs Popularity',
                 labels={
                     'members': 'Member Count (Log Scale)',
                     'recommendation_ratio': 'Recommendation Ratio (Recs per Member)',
                     'score': 'Score'
                 },
                 color_continuous_scale='Viridis',
                 log_x=True)

# Add median lines
fig.add_vline(x=median_members, line_dash="dash", line_color="black", line_width=2,
              annotation_text="Median Members", annotation_position="top")
fig.add_hline(y=median_rec_ratio, line_dash="dash", line_color="black", line_width=2,
              annotation_text="Median Rec Ratio", annotation_position="right")

# Add zones annotation with BRIGHT VISIBLE COLORS
fig.add_annotation(x=2.5, y=0.008, 
                   text="<b>Hidden Gems</b><br>(High Recs, Low Members)", 
                   showarrow=False, 
                   font=dict(size=14, color="white"), 
                   bgcolor="rgba(255, 50, 50, 0.9)",  # BRIGHT RED background
                   bordercolor="darkred",
                   borderwidth=2,
                   borderpad=8)

fig.add_annotation(x=5.8, y=0.0003, 
                   text="<b>Mainstream</b><br>(High Members, Low Rec Ratio)", 
                   showarrow=False, 
                   font=dict(size=14, color="white"),
                   bgcolor="rgba(20, 180, 20, 0.9)",  # BRIGHT GREEN background
                   bordercolor="darkgreen",
                   borderwidth=2,
                   borderpad=8)

fig.update_layout(
    height=600,
    hovermode='closest',
    showlegend=True,
    plot_bgcolor='rgba(240, 240, 240, 0.8)',
    paper_bgcolor='white'
)

fig.show()


**Key Insight:** Low-member anime with high recommendation ratios are hidden gems worth promoting. Strategic marketing could turn passionate niche audiences into mainstream success.


---

## Question 2: Passion vs. Popularity Paradox

**Research Question:** Which anime have high favorite intensity but low scores (cult classics vs mainstream hits)?

In [25]:
# Q2: Passion vs. Popularity Paradox
df_q2 = df[(df['score'].notna()) & (df['favorite_intensity'] > 0) & (df['members'] > 100)].copy()

median_score = df_q2['score'].median()
median_fav = df_q2['favorite_intensity'].median()

df_q2['quadrant'] = 'Average'
df_q2.loc[(df_q2['favorite_intensity'] >= median_fav) & (df_q2['score'] >= median_score), 'quadrant'] = 'Mainstream Hits'
df_q2.loc[(df_q2['favorite_intensity'] >= median_fav) & (df_q2['score'] < median_score), 'quadrant'] = 'Cult Classics'
df_q2.loc[(df_q2['favorite_intensity'] < median_fav) & (df_q2['score'] >= median_score), 'quadrant'] = 'Critically Acclaimed'

cult = df_q2[df_q2['quadrant'] == 'Cult Classics'].nlargest(10, 'favorite_intensity')[['title', 'score', 'favorite_intensity', 'user_favorites_count']]

print("=== TOP 10 CULT CLASSICS ===")
for idx, row in cult.iterrows():
    print(f"{row['title'][:40]:40} | Score: {row['score']:.2f} | Fav Int: {row['favorite_intensity']:.4f}")
print(f"\nQuadrant Counts: {df_q2['quadrant'].value_counts().to_dict()}")

=== TOP 10 CULT CLASSICS ===
Spacy                                    | Score: 5.38 | Fav Int: 0.0075
Moonflowers                              | Score: 5.49 | Fav Int: 0.0074
Shanshui Qing                            | Score: 6.57 | Fav Int: 0.0064
Lina Poe Poe                             | Score: 4.92 | Fav Int: 0.0060
Kagirinaki Rakuen                        | Score: 6.59 | Fav Int: 0.0058
Uobbuchou                                | Score: 5.16 | Fav Int: 0.0056
Zhan Shuang Panini                       | Score: 6.59 | Fav Int: 0.0053
Mayday                                   | Score: 6.56 | Fav Int: 0.0051
The Flying Luna Clipper                  | Score: 5.90 | Fav Int: 0.0050
Tian Xin Ge Ge                           | Score: 6.45 | Fav Int: 0.0049

Quadrant Counts: {'Mainstream Hits': 2795, 'Average': 2787, 'Critically Acclaimed': 1935, 'Cult Classics': 1928}


In [26]:
# Visualization: Scatter plot comparing Score vs Favorite Intensity
fig = px.scatter(df_q2, x='score', y='favorite_intensity', 
                 color='quadrant', 
                 hover_data=['title', 'members'],
                 title='Passion vs. Popularity: Score vs Favorite Intensity',
                 labels={'score': 'Critical Score', 'favorite_intensity': 'Favorite Intensity (Favs/Member)'},
                 color_discrete_map={
                     'Mainstream Hits': '#FF6B6B',
                     'Average': '#4ECDC4', 
                     'Critically Acclaimed': '#45B7D1',
                     'Cult Classics': '#FFA07A'
                 })

fig.add_hline(y=median_fav, line_dash="dash", line_color="gray", annotation_text="Median Fav Intensity")
fig.add_vline(x=median_score, line_dash="dash", line_color="gray", annotation_text="Median Score")
fig.update_layout(height=600)
fig.show()

**Key Insight:** Cult classics have intense fan devotion despite polarizing scores. These dedicated communities drive long-term engagement and merchandise sales beyond initial ratings.


---

## Question 3: Genre Dominance Over Time

**Research Question:** How has genre popularity shifted across different decades?



In [27]:
# Q3: Genre Dominance Over Time - PROPERLY HANDLE LIST STRINGS
import ast  # For safely parsing string lists

# Extract top genres and analyze their growth over decades
df_q3 = df[(df['genres'].notna()) & (df['year'].notna())].copy()
df_q3['decade'] = (df_q3['year'] // 10) * 10

# FIXED: Properly parse the genre lists and clean them
def parse_genres(genre_str):
    """Parse genre string like "['Action', 'Comedy']" into actual list"""
    try:
        # If it's already a list, return it
        if isinstance(genre_str, list):
            return genre_str
        # If it's a string representation of a list, parse it
        if isinstance(genre_str, str):
            # Handle empty brackets
            if genre_str.strip() in ['[]', '']:
                return []
            # Try to parse as Python literal
            return ast.literal_eval(genre_str)
    except:
        return []

# Apply parsing and filter out empty genre lists
df_q3['genres_parsed'] = df_q3['genres'].apply(parse_genres)
df_q3 = df_q3[df_q3['genres_parsed'].apply(len) > 0]  # Remove rows with no genres

# Explode genres properly
genres_exploded = df_q3.explode('genres_parsed')['genres_parsed']
top_genres = genres_exploded.value_counts().head(8).index.tolist()

# Create genre presence columns
for genre in top_genres:
    df_q3[genre] = df_q3['genres_parsed'].apply(lambda x: genre in x)

# Group by decade and count genre occurrences
genre_trends = df_q3.groupby('decade')[top_genres].sum().reset_index()
genre_trends_melted = genre_trends.melt(id_vars='decade', var_name='genre', value_name='count')

print("Top 8 Genres:")
print(top_genres)
print("\nGenre trends by decade:")
print(genre_trends)


Top 8 Genres:
['Comedy', 'Fantasy', 'Action', 'Adventure', 'Sci-Fi', 'Drama', 'Romance', 'Slice of Life']

Genre trends by decade:
    decade  Comedy  Fantasy  Action  Adventure  Sci-Fi  Drama  Romance  \
0  1910.00      13        1       0          0       0      7        0   
1  1920.00       7        7       3          4       0      4        1   
2  1930.00      20       14      19         19       1      4        2   
3  1940.00       8        6       5          4       0      3        0   
4  1950.00      10       11       2          6       0      3        1   
5  1960.00      53       35      46         64      36     31        6   
6  1970.00      76       57     102        134     104     93       22   
7  1980.00     372      208     343        341     352    253      121   
8  1990.00     759      527     596        585     455    420      217   
9  2000.00    1562      933     940        861     774    768      546   
10 2010.00    3164     2153    1868       1253    1047 

In [28]:
# Visualization: Line chart showing genre trends over time
fig = px.line(genre_trends_melted, x='decade', y='count', color='genre',
              title='Genre Evolution: Tracking Popularity Across Decades',
              labels={'decade': 'Decade', 'count': 'Number of Anime', 'genre': 'Genre'},
              markers=True)
fig.update_layout(height=500, hovermode='x unified')
fig.show()

**Key Insight:** Action, Comedy, and Fantasy dominated the 2010s boom but have declined since 2020. The market is ripe for fresh genres and innovative storytelling.


---

## Question 4: Studio Success Metrics

**Research Question:** Which studios consistently produce high-quality anime, and what is their output volume?




In [29]:
# Q4: Studio Success Metrics
df_q4 = df[(df['studios'].notna()) & (df['score'].notna())].copy()

# Explode studios and calculate metrics
studios_exploded = df_q4.assign(studio=df_q4['studios'].str.split(', ')).explode('studio')
studio_metrics = studios_exploded.groupby('studio').agg({
    'score': 'mean',
    'mal_id': 'count',  # FIXED: Changed from 'anime_id' to 'mal_id'
    'members': 'mean'
}).rename(columns={'mal_id': 'anime_count', 'members': 'avg_members'})

# Filter for studios with at least 10 anime and above median score
median_studio_score = studio_metrics['score'].median()
top_studios = studio_metrics[
    (studio_metrics['anime_count'] >= 10) & 
    (studio_metrics['score'] > median_studio_score)
].sort_values('score', ascending=False).head(15)

print("Top 15 Studios (Quality + Quantity):")
print(top_studios.round(2))

# Visualization: Bubble chart
fig = px.scatter(top_studios.reset_index(), 
                 x='anime_count', y='score', 
                 size='avg_members', 
                 hover_data=['studio'],
                 text='studio',
                 title='Studio Success: Balancing Quality and Quantity',
                 labels={'anime_count': 'Number of Anime Produced', 'score': 'Average Score'})
fig.update_traces(textposition='top center')
fig.update_layout(height=600)
fig.show()


Top 15 Studios (Quality + Quantity):
                      score  anime_count  avg_members
studio                                               
['Shuka']              7.80           19    124101.05
['Motion Magic']       7.79           14      8211.64
'Animation Do']        7.63           10    188055.00
['Kyoto Animation']    7.35          117    267317.56
['Kyoto Animation'     7.32           13    146926.92
['David Production']   7.32           47    304290.21
['CygamesPictures']    7.31           18     60402.94
['Gallop'              7.31           10    100674.60
'Xebec']               7.30           10     51552.40
['B.CMAY PICTURES']    7.30           19     59376.42
['TROYCA']             7.29           21     94950.24
['Bones']              7.29          151    345962.87
['Lerche']             7.29           65    262274.26
'CloverWorks']         7.28           11    548799.73
['White Fox']          7.28           46    430461.13


**Key Insight:** Top studios maintain 7+ scores while producing 10+ anime consistently. They're reliable partners with proven quality standards and audience trust.


---

## Question 5: Seasonal Release Strategy

**Research Question:** Is there an optimal season for anime releases based on engagement and ratings?



In [30]:
# Q5: Seasonal Release Strategy
df_q5 = df[(df['season'].notna()) & (df['score'].notna()) & (df['members'].notna())].copy()

# Calculate seasonal metrics
seasonal_metrics = df_q5.groupby('season').agg({
    'score': 'mean',
    'members': 'mean',
    'mal_id': 'count'  # FIXED: Changed from 'anime_id' to 'mal_id'
}).rename(columns={'mal_id': 'total_anime'})

print("Seasonal Performance Metrics:")
print(seasonal_metrics.round(2))

# Visualization: Box plot for score distribution by season
fig = px.box(df_q5, x='season', y='score',
             color='season',
             title='Seasonal Release Performance: Score Distribution',
             labels={'season': 'Season', 'score': 'Score'},
             category_orders={'season': ['Winter', 'Spring', 'Summer', 'Fall']})
fig.update_layout(height=500, showlegend=False)
fig.show()


Seasonal Performance Metrics:
        score  members  total_anime
season                             
Fall     6.49 68676.03         4421
Spring   6.48 63041.97         4839
Summer   6.40 58075.56         4380
Winter   6.23 48342.19         5005


**Key Insight:** Season timing has minimal impact on ratings - quality matters more. However, avoiding overcrowded release windows still helps visibility.


---

## Question 6: Content Length Preferences

**Research Question:** How does the number of episodes correlate with audience ratings and engagement?




In [31]:
# Q6: Content Length Preferences
df_q6 = df[(df['episodes'].notna()) & (df['score'].notna()) & (df['episodes'] > 0)].copy()

# Create episode buckets
df_q6['episode_bucket'] = pd.cut(df_q6['episodes'], bins=[0, 12, 24, 50, 100, 500], 
                                  labels=['1-12 (Short)', '13-24 (Standard)', '25-50 (Long)', '51-100 (Very Long)', '100+ (Epic)'])

episode_analysis = df_q6.groupby('episode_bucket').agg({
    'score': 'mean',
    'members': 'mean',
    'mal_id': 'count'  # FIXED: Changed from 'anime_id' to 'mal_id'
}).rename(columns={'mal_id': 'count'})

print("Episode Count Analysis:")
print(episode_analysis.round(2))

# Visualization: Bar chart with dual axis
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x=episode_analysis.index.astype(str), y=episode_analysis['count'], 
                      name='Number of Anime', marker_color='lightblue'), secondary_y=False)
fig.add_trace(go.Scatter(x=episode_analysis.index.astype(str), y=episode_analysis['score'], 
                          name='Avg Score', mode='lines+markers', marker_color='red', line=dict(width=3)), 
                          secondary_y=True)
fig.update_layout(title='Content Length Sweet Spot: Episodes vs Performance', height=500)
fig.update_xaxes(title_text="Episode Range")
fig.update_yaxes(title_text="Number of Anime", secondary_y=False)
fig.update_yaxes(title_text="Average Score", secondary_y=True)
fig.show()


Episode Count Analysis:
                    score   members  count
episode_bucket                            
1-12 (Short)         6.28  44211.14  14807
13-24 (Standard)     6.87 157658.36   1643
25-50 (Long)         6.84  96115.35   1372
51-100 (Very Long)   6.74  46738.20    531
100+ (Epic)          6.96 182868.55    168


**Key Insight:** 13-24 episodes is the sweet spot with highest scores (6.87). Long series can succeed too, but require exceptional quality to keep viewers engaged.


---

## Question 7: Rating Distribution & Polarization Analysis

**Research Question:** Which anime are most polarizing (high variance in user ratings) vs universally loved?




In [32]:
# Q7: Rating Distribution & Polarization Analysis
df_q7 = df[(df['score'].notna()) & (df['polarization_index'].notna()) & (df['scored_by'] > 1000)].copy()

# Categorize by polarization
median_polarization = df_q7['polarization_index'].median()
median_score = df_q7['score'].median()

df_q7['category'] = 'Average'
df_q7.loc[(df_q7['polarization_index'] > median_polarization) & (df_q7['score'] > median_score), 'category'] = 'Polarizing & High Rated'
df_q7.loc[(df_q7['polarization_index'] > median_polarization) & (df_q7['score'] <= median_score), 'category'] = 'Polarizing & Low Rated'
df_q7.loc[(df_q7['polarization_index'] <= median_polarization) & (df_q7['score'] > median_score), 'category'] = 'Universally Loved'
df_q7.loc[(df_q7['polarization_index'] <= median_polarization) & (df_q7['score'] <= median_score), 'category'] = 'Universally Mediocre'

print("Category Distribution:")
print(df_q7['category'].value_counts())
print("\nTop 5 Most Polarizing (High Rated):")
print(df_q7[df_q7['category'] == 'Polarizing & High Rated'].nlargest(5, 'polarization_index')[['title', 'score', 'polarization_index']])

# Visualization: Scatter plot
fig = px.scatter(df_q7, 
                 x='score', 
                 y='polarization_index',
                 color='category',
                 size='scored_by',
                 hover_data=['title', 'score', 'polarization_index', 'scored_by'],
                 title='Polarization vs Rating: Love It or Hate It?',
                 labels={'score': 'Average Score', 'polarization_index': 'Polarization Index'},
                 color_discrete_map={
                     'Universally Loved': '#2ECC71',
                     'Polarizing & High Rated': '#F39C12',
                     'Polarizing & Low Rated': '#E74C3C',
                     'Universally Mediocre': '#95A5A6',
                     'Average': '#BDC3C7'
                 })

fig.add_vline(x=median_score, line_dash="dash", line_color="gray")
fig.add_hline(y=median_polarization, line_dash="dash", line_color="gray")
fig.update_layout(height=600, hovermode='closest')
fig.show()


Category Distribution:
category
Universally Mediocre       3339
Polarizing & High Rated    3279
Polarizing & Low Rated     1990
Universally Loved          1962
Name: count, dtype: int64

Top 5 Most Polarizing (High Rated):
                      title  score  polarization_index
7085     Gintama: The Final   9.05               60.70
22532     Sousou no Frieren   9.29               56.80
7000   Ginga Eiyuu Densetsu   9.02               54.60
7089               Gintama°   9.05               51.70
17434  One Piece Fan Letter   9.03               51.60


**Key Insight:** Polarizing anime drive conversation and community engagement. Love-it-or-hate-it content builds dedicated fan bases even without universal appeal.


---

## Question 8: Source Material Performance

**Research Question:** Do anime adapted from manga perform better than original stories or light novels?




In [33]:
# Q8: Source Material Performance
df_q8 = df[(df['source'].notna()) & (df['score'].notna()) & (df['members'] > 5000)].copy()

# Get top 6 source types
top_sources = df_q8['source'].value_counts().head(6).index.tolist()
df_q8_filtered = df_q8[df_q8['source'].isin(top_sources)]

# Calculate metrics by source
source_metrics = df_q8_filtered.groupby('source').agg({
    'score': 'mean',
    'members': 'mean',
    'mal_id': 'count'
}).rename(columns={'mal_id': 'count'}).sort_values('score', ascending=False)

print("Source Material Performance:")
print(source_metrics.round(2))

# Visualization: Violin plot
fig = px.violin(df_q8_filtered, 
                x='source', 
                y='score',
                color='source',
                box=True,
                points='outliers',
                title='Source Material Performance: Score Distribution',
                labels={'source': 'Source Material', 'score': 'Score'},
                category_orders={'source': source_metrics.index.tolist()})

fig.update_layout(height=600, showlegend=False)
fig.show()


Source Material Performance:
              score   members  count
source                              
Manga          7.13 150283.20   3451
Light novel    7.03 237116.66    955
Web manga      6.99 167575.12    316
Original       6.82  82646.88   1811
Game           6.65  46957.61    563
Visual novel   6.59  57095.28    766


**Key Insight:** Manga adaptations perform best with built-in audiences. Original anime can achieve critical success but need stronger marketing from scratch.


---

## Question 9: Anime Format Impact

**Research Question:** How do different formats (TV, Movie, OVA, Special) perform in terms of ratings and popularity?




In [34]:
# Q9: Anime Format Analysis
df_q9 = df[(df['type'].notna()) & (df['score'].notna())].copy()

# Calculate format metrics
format_metrics = df_q9.groupby('type').agg({
    'score': 'mean',
    'members': 'mean',
    'mal_id': 'count',
    'episodes': 'mean'
}).rename(columns={'mal_id': 'count'}).sort_values('count', ascending=False)

print("Format Performance Metrics:")
print(format_metrics.round(2))

# Visualization: Grouped bar chart
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Average Score by Format', 'Popularity (Avg Members) by Format'),
    specs=[[{"secondary_y": False}, {"secondary_y": False}]]
)

# Score chart
fig.add_trace(
    go.Bar(x=format_metrics.index, y=format_metrics['score'], 
           name='Avg Score', marker_color='#3498DB'),
    row=1, col=1
)

# Members chart
fig.add_trace(
    go.Bar(x=format_metrics.index, y=format_metrics['members'], 
           name='Avg Members', marker_color='#E74C3C'),
    row=1, col=2
)

fig.update_xaxes(title_text="Format", row=1, col=1)
fig.update_xaxes(title_text="Format", row=1, col=2)
fig.update_yaxes(title_text="Average Score", row=1, col=1)
fig.update_yaxes(title_text="Average Members", row=1, col=2)

fig.update_layout(height=500, title_text="Anime Format Impact on Performance", showlegend=False)
fig.show()


Format Performance Metrics:
            score   members  count  episodes
type                                        
TV           6.83 166149.26   5084     30.39
OVA          6.24  17848.25   3452      2.45
Movie        6.37  41803.02   2821      1.10
ONA          6.26  14028.17   2363     13.34
Music        5.95   1338.03   2308      1.11
Special      6.40  19648.15   1469      2.86
TV Special   6.47  23918.82    584      1.43
CM           5.69   2504.11    377      2.39
PV           6.09   3782.35    202      1.21


**Key Insight:** TV series dominate engagement through episodic storytelling. Movies offer quality over quantity, while OVAs serve dedicated niche audiences effectively.


---

## Question 10: Completion Rate & Drop Rate Patterns

**Research Question:** What factors correlate with high completion rates vs high drop rates?




In [35]:
# Q10: Completion Rate Analysis
df_q10 = df[(df['completion_rate'].notna()) & (df['drop_rate'].notna()) & 
            (df['total'] > 1000) & (df['score'].notna()) & (df['episodes'].notna())].copy()

# Categorize by completion rate
high_completion = df_q10['completion_rate'].quantile(0.75)
high_drop = df_q10['drop_rate'].quantile(0.75)

df_q10['engagement_type'] = 'Average'
df_q10.loc[df_q10['completion_rate'] >= high_completion, 'engagement_type'] = 'High Completion'
df_q10.loc[df_q10['drop_rate'] >= high_drop, 'engagement_type'] = 'High Drop Rate'
df_q10.loc[(df_q10['completion_rate'] >= high_completion) & (df_q10['drop_rate'] < high_drop), 'engagement_type'] = 'Binge-Worthy'

print("Engagement Type Distribution:")
print(df_q10['engagement_type'].value_counts())
print("\nTop 10 Most Binge-Worthy (High Completion, Low Drop):")
print(df_q10[df_q10['engagement_type'] == 'Binge-Worthy'].nlargest(10, 'completion_rate')[['title', 'score', 'completion_rate', 'drop_rate']])

# Visualization: Scatter plot with better colors
df_q10_viz = df_q10[df_q10['episodes'] > 0].copy()

fig = px.scatter(df_q10_viz, 
                 x='completion_rate', 
                 y='drop_rate',
                 color='score',
                 size='episodes',
                 hover_data=['title', 'score', 'episodes', 'completion_rate', 'drop_rate'],
                 title='Completion vs Drop Rate: What Keeps Viewers Engaged?',
                 labels={'completion_rate': 'Completion Rate (%)', 'drop_rate': 'Drop Rate (%)'},
                 color_continuous_scale='Viridis')  # CHANGED: Better color scale

fig.add_annotation(x=0.8, y=0.05, 
                   text="<b>Binge-Worthy Zone</b><br>(High Completion, Low Drop)", 
                   showarrow=False, 
                   font=dict(size=14, color="white"),
                   bgcolor="rgba(46, 204, 113, 0.9)",  # Bright green
                   bordercolor="darkgreen",
                   borderwidth=2,
                   borderpad=8)

fig.update_layout(height=600, hovermode='closest', plot_bgcolor='rgba(240, 240, 240, 0.8)')
fig.show()


Engagement Type Distribution:
engagement_type
Average           7083
High Drop Rate    3501
Binge-Worthy      3420
Name: count, dtype: int64

Top 10 Most Binge-Worthy (High Completion, Low Drop):
                                                   title  score  \
18606              Pokemon Movie 01: Mewtwo no Gyakushuu   7.67   
18607  Pokemon Movie 02: Maboroshi no Pokemon Lugia B...   7.35   
18608        Pokemon Movie 03: Kesshoutou no Teiou Entei   7.09   
18609        Pokemon Movie 04: Celebi Toki wo Koeta Deai   6.91   
11428                                   Katsudou Shashin   5.51   
5286                Dragon Ball Z Movie 14: Kami to Kami   7.42   
18610  Pokemon Movie 05: Mizu no Miyako no Mamorigami...   7.17   
5869       Fanren Xiu Xian Chuan: Xinghai Feichi Xuzhang   7.86   
18613   Pokemon Movie 08: Mew to Hadou no Yuusha Lucario   7.33   
18612       Pokemon Movie 07: Rekkuu no Houmonsha Deoxys   6.98   

       completion_rate  drop_rate  
18606            96.73       0

**Key Insight:** Binge-worthy shows balance compelling stories with optimal length. Pokemon movies lead here - established IPs with manageable runtimes maximize completion rates.
